# Symbolic expression for $J$ matrix

In [2]:
from sympy import *
import numpy as np
m11=Symbol('m11'); m12=Symbol('m12'); m21=Symbol('m21'); m22=Symbol('m22')
omega=Matrix([[0,1], [-1,0]])
pbar=Matrix([[m11,m12], [m21,m22]])
J=pbar @ omega @ pbar.inv()
simplify(J.subs(m11*m22 - m12*m21,1))

Matrix([
[-m11*m21 - m12*m22,   m11**2 + m12**2],
[  -m21**2 - m22**2, m11*m21 + m12*m22]])

# Basic linear optics code

In [3]:
import numpy as np
la=np.linalg 
# Drift
def DRIFT(L=1):
    '''
    This a  matrix for a L-long drift. 
    '''
    return np.array([[1, L],[0, 1]])
# Quadrupole
def QUAD(f=1):
    '''
    This a matrix for a this quadrupole of focal lenght f.
    '''
    return np.array([[1, 0],[-1/f,1]])
# One turn maps of 100 m long FODO cell with 50 m focal length.
def M_OTM(f=50):
    M_OTM=DRIFT(50)@QUAD(-f)@DRIFT(50)@QUAD(f)
    return M_OTM

eigenvalues,P= la.eig(M_OTM())   # P is >>before the normalization<<
P=P/((la.det(P)*1j)**(1/len(P))) # P is >>after the normalization<<
D=np.diag(eigenvalues)
# Compute beta and alpha
beta=np.real(P[0,0]**2*2)
alpha=-np.real(P[1,0]*np.sqrt(2*beta))
print('The cell phase advance is ' + str(np.rad2deg(np.angle(D)[0][0])) + ' deg.')
print('The periodic beta at the start of the cell is '+ str(beta)+ ' m.')
print('The periodic alpha at the start of the cell is '+ str(alpha)+'.')

The cell phase advance is 60.00000000000001 deg.
The periodic beta at the start of the cell is 173.20508075688772 m.
The periodic alpha at the start of the cell is -1.7320508075688774.


# From the matrix to the polynominal form of the $J_{CS}$

In [4]:
from sympy import *
alpha=Symbol('alpha');beta=Symbol('beta');gamma=Symbol('gamma');
x=Symbol('x');px=Symbol('px')
omega=Matrix([[0,1], [-1,0]])
J=Matrix([[alpha, beta], [-gamma,-alpha]]); X=Matrix([[x],[px]])
expand(1/2*X.T@omega@J.inv()@X)[0,0].subs(alpha**2 - beta*gamma,-1)

1.0*alpha*px*x + 0.5*beta*px**2 + 0.5*gamma*x**2

# The phase advance computation

In [6]:
import sympy as sy
beta0=sy.Symbol('beta0');alpha0=sy.Symbol('alpha0');
beta1=sy.Symbol('beta1');alpha1=sy.Symbol('alpha1');
m11=sy.Symbol('m11');m12=sy.Symbol('m12');m21=sy.Symbol('m21');m22=sy.Symbol('m22');

Pbar0=sy.Matrix([[sy.sqrt(beta0),0], [-alpha0/sy.sqrt(beta0),1/sy.sqrt(beta0)]])
Pbar1=sy.Matrix([[sy.sqrt(beta1),0], [-alpha1/sy.sqrt(beta1),1/sy.sqrt(beta1)]])
M=sy.Matrix([[m11, m12],[m21, m22]])
pprint(sy.simplify(Pbar1.inv()@M@Pbar0))

⎡              -α₀⋅m₁₂ + β₀⋅m₁₁                      m₁₂      ⎤
⎢              ────────────────                 ───────────── ⎥
⎢                 ____   ____                     ____   ____ ⎥
⎢               ╲╱ β₀ ⋅╲╱ β₁                    ╲╱ β₀ ⋅╲╱ β₁  ⎥
⎢                                                             ⎥
⎢-α₀⋅(α₁⋅m₁₂ + β₁⋅m₂₂) + β₀⋅(α₁⋅m₁₁ + β₁⋅m₂₁)  α₁⋅m₁₂ + β₁⋅m₂₂⎥
⎢────────────────────────────────────────────  ───────────────⎥
⎢                 ____   ____                     ____   ____ ⎥
⎣               ╲╱ β₀ ⋅╲╱ β₁                    ╲╱ β₀ ⋅╲╱ β₁  ⎦


# Transport matrix as function of the optics parameter

In [7]:
import sympy as sy
beta1=sy.Symbol('beta1');alpha1=sy.Symbol('alpha1');
beta2=sy.Symbol('beta2');alpha2=sy.Symbol('alpha2');
phi=sy.Symbol('phi');Q=sy.Symbol('Q');theta1=sy.Symbol('theta1');
Pbar1=sy.Matrix([[sy.sqrt(beta1),0], [-alpha1/sy.sqrt(beta1),1/sy.sqrt(beta1)]])
Pbar2=sy.Matrix([[sy.sqrt(beta2),0], [-alpha2/sy.sqrt(beta2),1/sy.sqrt(beta2)]])
R=sy.Matrix([[sy.cos(phi),sy.sin(phi)], [-sy.sin(phi),sy.cos(phi)]])
sy.simplify(Pbar2@R@Pbar1.inv())

Matrix([
[                                              sqrt(beta2)*(alpha1*sin(phi) + cos(phi))/sqrt(beta1),                      sqrt(beta1)*sqrt(beta2)*sin(phi)],
[(-alpha1*alpha2*sin(phi) + alpha1*cos(phi) - alpha2*cos(phi) - sin(phi))/(sqrt(beta1)*sqrt(beta2)), sqrt(beta1)*(-alpha2*sin(phi) + cos(phi))/sqrt(beta2)]])

# Closed orbit computation

In [9]:
import sympy as sy
beta1=sy.Symbol('beta1');alpha1=sy.Symbol('alpha1');
beta2=sy.Symbol('beta2');alpha2=sy.Symbol('alpha2');
Q=sy.Symbol('Q');theta1=sy.Symbol('theta1');phi=sy.Symbol('phi')

J=sy.Matrix([[alpha1, beta1],[-(1+alpha1**2)/beta1,-alpha1]])
I=sy.Matrix([[1, 0],[0,1]])
MCO=sy.simplify((I-(I*sy.cos(2*sy.pi*Q)+J*sy.sin(2*sy.pi*Q))).inv())
X0=sy.simplify(MCO@sy.Matrix([[0],[theta1]]))
T=sy.Matrix([[(sy.sqrt(beta2)*(sy.cos(phi)+alpha1*sy.sin(phi)))/sy.sqrt(beta1),\
              sy.sqrt(beta1)*sy.sqrt(beta2)*sy.sin(phi)],\
            [-((-alpha1+alpha2)*sy.cos(phi)+sy.sin(phi)+alpha1*alpha2*sy.sin(phi))/sy.sqrt(beta1)/sy.sqrt(beta2),\
            sy.sqrt(beta1)*(sy.cos(phi)-alpha2*sy.sin(phi))/sy.sqrt(beta2)]])
sy.simplify(T@X0)

Matrix([
[                                                 sqrt(beta1)*sqrt(beta2)*theta1*(sin(phi) + cos(phi)/tan(pi*Q))/2],
[-sqrt(beta1)*theta1*(alpha2*sin(phi) + alpha2*cos(phi)/tan(pi*Q) + sin(phi)/tan(pi*Q) - cos(phi))/(2*sqrt(beta2))]])